# Gradient Descent Methods

### Author: Aymeric DIEULEVEUT

### <font color='Blue'> Read the following two cells before you start clicking everywhere !! </font> :D

The aim of this material is to implement and compare several optimization methods for Least Squares Regression and Logistic Regression. We focus on the empirical risk minimization problem.

To do so we will:

| Part | Objective | What you have to code |
| :- |:- | :- |
| I. | Simulate a linear and logistic model | <font color='green'>nothing !</font>|
| II. | Create two classes: ModelLinReg and ModelLogisticReg,| <font color='orange'> Loss and gradients  for the logistic loss </font>|
|| this will allow us to access the gradients and Lipshitz/Smoothness constants of the loss functions|
|III. | Code some methods listed afterwards: GD, SGD, AGD, SVRG, etc. |  <font color='orange'> The update steps</font>|
| |only the most crucial part -- the update step  -- has to be implemented|
|IV. | Compare the methods of your choice|<font color='green'>nearly nothing: choose your methods </font> |



##### Main methods 
- gradient descent (GD)
- accelerated gradient descent (AGD)
- coordinate gradient descent (CD)
- stochastic gradient descent (SGD)
- stochastic variance reduced gradient descent (SVRG)
- optimization methods for Deep Learning

### Remarks
##### Most of the content is elementary, but serves multiple objectives ...
- hands on on the optimization methods you have encountered
- compare optimization methods (stochastic vs non-stochastic), impact of Variance reduction
- what can we read on convergence curves: deduct convergence speed from the learning curve
- how to obtain a meaningful optimization curve

##### and can be extended in **many** directions
- framework to play with hyper-parameters 
- framework to implement other methods
- back to test error: what happens?
- adapative methods, non uniform sampling in stochastic, federated learning methods, etc.

# How this lab works


## Organisation 
- Most of the content is already implemented (obviously)
- You have to complete the code when there is a blank with
````   
        #
        #
        # YOUR CODE HERE
        #
        #
````
- A  corrected version will be put online at the end 

## Interactive tool
To follow your progress, adapt correction spped, and provide better feedback, we have developped a tool with Evan Courdier at EPFL:
- At the beginning of the lab, when running the first cell, you will be able to enter your name
- Afterwards, each time a ```send``` function appears, the first argument of the send function (typically the code of your function, a value of an array, a plot, etc), is send to a server, which allows me to follwo your progress, correct some mistakes, etc.
- This is totally transparent for you. The code is OS, all results are erased afterwards. You can use a pseudo if you want (try to make it unique). 



<font color='green'> If it works: </font> you will get a <Response [200]> message after each send. Thank you for helping me give a more interactive (hopefully better) lab!
<font color='orange'> If it does not, or if really do not want to use the tool </font> Do not try debugging it :D. Just redefine the send function as:    ```def send(a,b): return()```






# Table of content

[1. Introduction](#intro)<br>

[2. Models gradients and losses](#models)<br>

[2.1  Linear regression](#models_regression)<br>
[2.2  Check for Linear regression](#models_regression_check)<br>
[2.3  Logistic regression](#models_logistic)<br>
[2.4  Check for logistic regression](#models_logistic_check)<br>


[3. Solvers](#solvers)<br>

[3.1 Tools for solvers](#tools)<br>
[3.2 Gradient descent](#gd)<br>
[3.3 Accelerated Gradient descent](#agd)<br>
[3.4 Coordinate Gradient descent](#cgd)<br>
[3.5 Stochastic Gradient descent](#sgd)<br>
[3.6 Stochastic Average Gradient descent](#sag)<br>
[3.7 Stochastic Variance Reduced Gradient descent](#svrg)<br>
[3.8 Adagrad](#adagrad)<br>
[3.9 RMSProp](#rmsprop)<br>
[3.10 AdaDelta](#adadelta)<br>
[3.11 Adam](#adam)<br>
[3.12 Adamax](#adamax)<br>

[4. Comparison of all algorithms](#comparison)<br>

<a id='intro'></a>
# 1. Introduction

## 1.1. Getting model weights

We'll start by generating sparse vectors and simulating data

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

%matplotlib inline

np.set_printoptions(precision=2)  # to have simpler print outputs with numpy

## 1.2. Simulation of a linear model

In [ ]:
from numpy.random import multivariate_normal
from scipy.linalg.special_matrices import toeplitz
from numpy.random import randn

import requests
exec(requests.get("https://courdier.pythonanywhere.com/get-send-code").content)
npt_config = {
    'session_name': 'Optimization-Gradient-Methods',
    'session_owner': 'aymeric',
    'sender_name': input("Your name:"),
}
send('start', 0)    

In [ ]:
def simu_linreg(w0, n_samples=1000, corr=0.5, std=0.5):
    """Simulation of a linear regression model with Gaussian features
    and a Toeplitz covariance, with Gaussian noise.
    
    Parameters
    ----------
    w0 : `numpy.array`, shape=(n_features,)
        Model weights
    
    n_samples : `int`, default=1000
        Number of samples to simulate
    
    corr : `float`, default=0.5
        Correlation of the features
    
    std : `float`, default=0.5
        Standard deviation of the noise

    Returns
    -------
    X : `numpy.ndarray`, shape=(n_samples, n_features)
        Simulated features matrix. It contains samples of a centered 
        Gaussian  vector with Toeplitz covariance.
    
    y : `numpy.array`, shape=(n_samples,)
        Simulated labels
    """
    n_features = w0.shape[0]
    # Construction of a covariance matrix
    cov = toeplitz(corr ** np.arange(0, n_features))
    # Simulation of features
    X = multivariate_normal(np.zeros(n_features), cov, size=n_samples)
    # Simulation of the labels
    y = X.dot(w0) + std * randn(n_samples)
    return X, y

In [ ]:
n_samples = 500
w0 = np.array([0.5])

X, y = simu_linreg(w0, n_samples=n_samples, corr=0.3, std=0.5)
plt.scatter(X, y)
plt.xlabel(r"$x_i$", fontsize=16)
plt.ylabel(r"$y_i$", fontsize=16)
plt.title("Linear regression simulation", fontsize=18)
plt.scatter(X, y, label='data')
plt.legend()
send(plt, 1)

## 1.3. Simulation of a logistic regression model

In [ ]:
def sigmoid(t):
    """Sigmoid function (overflow-proof)"""
    idx = t > 0
    out = np.empty(t.size)    
    out[idx] = 1 / (1. + np.exp(-t[idx]))
    exp_t = np.exp(t[~idx])
    out[~idx] = exp_t / (1. + exp_t)
    return out

def simu_logreg(w0, n_samples=1000, corr=0.5):
    """Simulation of a logistic regression model with Gaussian features
    and a Toeplitz covariance.
    
    Parameters
    ----------
    w0 : `numpy.array`, shape=(n_features,)
        Model weights
    
    n_samples : `int`, default=1000
        Number of samples to simulate
    
    corr : `float`, default=0.5
        Correlation of the features

    Returns
    -------
    X : `numpy.ndarray`, shape=(n_samples, n_features)
        Simulated features matrix. It contains samples of a centered 
        Gaussian vector with Toeplitz covariance.
    
    y : `numpy.array`, shape=(n_samples,)
        Simulated labels
    """
    n_features = w0.shape[0]
    cov = toeplitz(corr ** np.arange(0, n_features))
    X = multivariate_normal(np.zeros(n_features), cov, size=n_samples)
    p = sigmoid(X.dot(w0))
    y = np.random.binomial(1, p, size=n_samples)
    # Put the label in {-1, 1}
    y[:] = 2 * y - 1
    return X, y

In [ ]:
u = np.array([1,2,3])
sigmoid(u)

In [ ]:
n_samples = 500
w0 = np.array([-3, 3.])

X, y = simu_logreg(w0, n_samples=n_samples, corr=0.4)

plt.scatter(*X[y == 1].T, color='b', s=10, label=r'$y_i=1$')
plt.scatter(*X[y == -1].T, color='r', s=10, label=r'$y_i=-1$')
plt.legend(loc='upper left')
plt.xlabel(r"$x_i^1$", fontsize=16)
plt.ylabel(r"$x_i^2$", fontsize=16)
plt.title("Logistic regression simulation", fontsize=18)
send(plt, 2)

<a id='models'></a>
# 2. Models gradients and losses

We want to minimize a goodness-of-fit function $f$ with ridge regularization, namely
$$
\arg\min_{w \in \mathbb R^d} \Big\{ f(w) + \frac{\lambda}{2} \|w\|_2^2 \Big\}
$$
where $d$ is the number of features and where we will assume that $f$ is $L$-smooth.
We will consider below the following cases.

**Linear regression**, where 
$$
f(w) = \frac 1n \sum_{i=1}^n f_i(w) = \frac{1}{2n} \sum_{i=1}^n (y_i - x_i^\top w)^2 + \frac{\lambda}{2} \|w\|_2^2 = \frac{1}{2 n} \| y - X w \|_2^2 + \frac{\lambda}{2} \|w\|_2^2,
$$
where $n$ is the sample size, $y = [y_1 \cdots y_n]$ is the vector of labels and $X$ is the matrix of features with lines containing the features vectors $x_i \in \mathbb R^d$.

**Logistic regression**, where
$$
f(w) = \frac 1n \sum_{i=1}^n f_i(w) = \frac{1}{n} \sum_{i=1}^n \log(1 + \exp(-y_i x_i^\top w)) + \frac{\lambda}{2} \|w\|_2^2,
$$
where $n$ is the sample size, and where labels $y_i \in \{ -1, 1 \}$ for all $i$.

We need to be able to compute $f(w)$ and its gradient $\nabla f(w)$, in order to solve this problem, as well as $\nabla f_i(w)$ for stochastic gradient descent methods and $\frac{\partial f(w)}{\partial w_j}$ for coordinate descent.

Below is the full implementation for linear regression.

<a id='models_regression'></a>

## 2.1 Linear regression

In [ ]:
from numpy.linalg import norm


class ModelLinReg:
    """A class giving first order information for linear regression
    with least-squares loss
    
    Parameters
    ----------
    X : `numpy.array`, shape=(n_samples, n_features)
        The features matrix
    
    y : `numpy.array`, shape=(n_samples,)
        The vector of labels
    
    strength : `float`
        The strength of ridge penalization
    """    
    def __init__(self, X, y, strength):
        self.X = X
        self.y = y
        self.strength = strength
        self.n_samples, self.n_features = X.shape
    
    def loss(self, w):
        """Computes f(w)"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        return 0.5 * norm(y - X.dot(w)) ** 2 / n_samples + strength * norm(w) ** 2 / 2
    
    def grad(self, w):
        """Computes the gradient of f at w"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        return X.T.dot(X.dot(w) - y) / n_samples + strength * w

    def grad_i(self, i, w):
        """Computes the gradient of f_i at w"""
        x_i = self.X[i]
        return (x_i.dot(w) - y[i]) * x_i + self.strength * w

    def grad_coordinate(self, j, w):
        """Computes the partial derivative of f with respect to 
        the j-th coordinate"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        return X[:, j].T.dot(X.dot(w) - y) / n_samples + strength * w[j]

    def lip(self):
        """Computes the Lipschitz constant of the gradients of  f"""
        X, n_samples = self.X, self.n_samples
        return norm(X.T.dot(X), 2) / n_samples + self.strength

    def lip_coordinates(self):
        """Computes the Lipschitz constant of the gradients of f with respect to 
        the j-th coordinate"""
        X, n_samples = self.X, self.n_samples
        return (X ** 2).sum(axis=0) / n_samples + self.strength
        
    def lip_max(self):
        """Computes the maximum of the lipschitz constants of the gradients of f_i"""
        X, n_samples = self.X, self.n_samples
        return ((X ** 2).sum(axis=1) + self.strength).max()
    
    def hessian(self):
        X, n_samples = self.X, self.n_samples
        return(X.T.dot(X))/ n_samples + self.strength

<a id='models_regression_check'></a>

## 2.2 Checks for the linear regression model

In [ ]:
## Simulation setting
n_features = 50
nnz = 20
idx = np.arange(n_features)
w0 = (-1) ** (idx + 1) * np.exp(-idx / 10.)
w0[nnz:] = 0.

plt.figure(figsize=(5, 3))
plt.stem(w0)
plt.title("Model weights")

In [ ]:
from scipy.optimize import check_grad

X, y = simu_linreg(w0, corr=0.6)
model = ModelLinReg(X, y, strength=1e-3)
w = np.random.randn(n_features)

send(float(check_grad(model.loss, model.grad, w)), 3)
print(check_grad(model.loss, model.grad, w)) # This must be a number (of order 1e-6)

In [ ]:
print("lip=", model.lip())
print("lip_max=", model.lip_max())
print("lip_coordinates=", model.lip_coordinates())

In [ ]:
model.hessian().shape

<a id='models_logistic'></a>

## 2.3 Logistic regression

**1) Compute (on paper) the gradient $\nabla f$, the gradient of $\nabla f_i$ and the gradient of the coordinate function $\frac{\partial f(w)}{\partial w_j}$ of $f$ for logistic regression (fill the class given below).**

**2) Fill in the functions below for the computation of $f$, $\nabla f$, $\nabla f_i$ and $\frac{\partial f(w)}{\partial w_j}$ for logistic regression in the ModelLogReg class below.**

In [ ]:
class ModelLogReg:
    """A class giving first order information for logistic regression
    
    Parameters
    ----------
    X : `numpy.array`, shape=(n_samples, n_features)
        The features matrix
    
    y : `numpy.array`, shape=(n_samples,)
        The vector of labels
    
    strength : `float`
        The strength of ridge penalization
    """    
    def __init__(self, X, y, strength):
        self.X = X
        self.y = y
        self.strength = strength
        self.n_samples, self.n_features = X.shape
    
    def loss(self, w):
        """Computes f(w)"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
       
    def grad(self, w):
        """Computes the gradient of f at w"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
    
    def grad_i(self, i, w):
        """Computes the gradient of f_i at w"""
        x_i = self.X[i]
        strength = self.strength
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
    
    def grad_coordinate(self, j, w):
        """Computes the partial derivative of f with respect to 
        the j-th coordinate"""
        y, X, n_samples, strength = self.y, self.X, self.n_samples, self.strength
        u = y*np.exp(- y * (X.dot(w)))/(1 + np.exp(- y * (X.dot(w))))
        return - (X[:, j].T.dot(u))/n_samples + strength * w[j]


    def lip(self):
        """Computes (an upper bound on) the Lipschitz constant of the gradient of  f"""
        X, n_samples = self.X, self.n_samples

        return norm(X.T.dot(X), 2) / (4*n_samples) + self.strength


    def lip_coordinates(self):
        """Computes (an upper bound on) the Lipschitz constant of the gradient of f with respect to 
        the j-th coordinate"""
        X, n_samples = self.X, self.n_samples

        return (X ** 2).sum(axis=0) / (4*n_samples) + self.strength


    def lip_max(self):
        """Computes (an upper bound on) the maximum of the lipschitz constants of the gradients of  f_i"""
        X, n_samples = self.X, self.n_samples
        return ((X ** 2).sum(axis=1)/4 + self.strength).max()

     
    def hessian(self):
        X, n_samples = self.X, self.n_samples
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        
send(ModelLogReg.loss, 4)
send(ModelLogReg.grad, 5)
send(ModelLogReg.grad_i, 6)


<a id='models_logistic_check'></a>


## 2.4 Checks for the logistic regression model

**3) Use the function `simu_logreg` to simulate data according to the logistic regression model. Check numerically the gradient using the function ``checkgrad`` from ``scipy.optimize``, as we did for linear regression above.**

In [ ]:
## Simulation setting
n_features = 50
nnz = 20
idx = np.arange(n_features)
w0 = (-1) ** (idx + 1) * np.exp(-idx / 10.)
w0[nnz:] = 0.

plt.figure(figsize=(5, 3))
plt.stem(w0)
plt.title("Model weights")

from scipy.optimize import check_grad




#
#
# YOUR CODE HERE
#
#

send('Checkgrad returns %.2e' % (check_grad(model.loss, model.grad, w)), 7)
print('Checkgrad returns %.2e' % (check_grad(model.loss, model.grad, w))) # This must be a number (of order 1e-6)


In [ ]:
print("lip=", model.lip())
print("lip_max=", model.lip_max())
print("lip_coordinates=", model.lip_coordinates())

<a id='solvers'></a>
## 3. Solvers

We now have classes `ModelLinReg` and `ModelLogReg` that allow to compute $f(w)$, $\nabla f(w)$, 
$\nabla f_i(w)$ and $\frac{\partial f(w)}{\partial w_j}$ for the objective $f$
given by linear and logistic regression. We want now to code and compare several solvers to minimize $f$.

<a id='tools'></a>
## 3.1. Tools for the solvers

The following tools store the loss after each epoch

In [ ]:
# Starting point of all solvers
w0 = np.zeros(model.n_features)

# Number of iterations
n_iter = 50

# Random samples indices for the stochastic solvers (sgd, sag, svrg) 
idx_samples = np.random.randint(0, model.n_samples, model.n_samples * n_iter)

In [ ]:
def inspector(model, n_iter, verbose=True):
    """A closure called to update metrics after each iteration.
    Don't even look at it, we'll just use it in the solvers."""
    objectives = []
    it = [0] # This is a hack to be able to modify 'it' inside the closure.
    def inspector_cl(w):
        obj = model.loss(w)
        objectives.append(obj)
        if verbose == True:
            if it[0] == 0:
                print(' | '.join([name.center(8) for name in ["it", "obj"]]))
            if it[0] % (n_iter / 5) == 0:
                print(' | '.join([("%d" % it[0]).rjust(8), ("%.6e" % obj).rjust(8)]))
            it[0] += 1
    inspector_cl.objectives = objectives
    return inspector_cl

<a id='gd'></a>
## 3.2 Gradient descent


**4) Finish the function `gd` below that implements the gradient descent algorithm and test it using the next cell.**

In [ ]:
def gd(model, w0, step,  n_iter, callback, verbose=True):
    """Gradient descent
    """
    #step = 1 / model.lip()
    w = w0.copy()
    w_new = w0.copy()
    if verbose:
        print("Lauching GD solver...")
    callback(w)
    for k in range(n_iter + 1):
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        callback(w)
    return w
send(gd, 8)

### The following code runs GD and stores the objectivre values

In [ ]:
callback_gd = inspector(model, n_iter=n_iter)
w_gd = gd(model, w0, step= 1/model.lip(),  n_iter=n_iter, callback=callback_gd)

- Which step size was chosen?
- What is the expected rate of convergence?

<a id='agd'></a>
## 3.3 Accelerated gradient descent

**5) Finish the function `agd` below that implements the accelerated gradient descent algorithm and test it using the next cell.**

What choice of momentum coefficient is recommended for AGD ?
- for strongly convex
- for convex functions

Here you can make different choices:
- an arbitrary value (0.9)
- using the strong convexity
- using only convexity

In [ ]:
def agd(model, w0, n_iter, callback, verbose=True):
    """Accelerated gradient descent
    """
    mu = model.strength
    step = 1 / model.lip()
    w = w0.copy()
    w_new = w0.copy()
    # An extra variable is required for acceleration
    z = w0.copy() # the auxiliari point at which the gradient is taken
    t = 1. # beta this morning = momentum coefficient 
    t_new = 1.    
    if verbose:
        print("Lauching AGD solver...")
    callback(w)
    for k in range(n_iter + 1):
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        callback(w)
    return w

send(agd, 9)

In [ ]:
callback_agd = inspector(model, n_iter=n_iter)
w_agd = agd(model, w0, n_iter=n_iter, callback=callback_agd)

<a id='cgd'></a>

## 3.4 Coordinate gradient descent

**6) Finish the function `cgd` below that implements the coordinate gradient descent algorithm and test it using the next cell.**

In [ ]:
def cgd(model, w0, n_iter, callback, verbose=True):
    """Coordinate gradient descent
    """
    w = w0.copy()
    n_features = model.n_features
    steps = 1 / model.lip_coordinates()
    if verbose:
        print("Lauching CGD solver...")
    callback(w)
    for k in range(n_iter + 1):
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        callback(w)
    return w
send(cgd, 10)

In [ ]:
callback_cgd = inspector(model, n_iter=n_iter)
w_cgd = cgd(model, w0, n_iter=n_iter, callback=callback_cgd)

<a id='sgd'></a>
## 3.5. Stochastic gradient descent

**7) Finish the function `sgd` below that implements the st stochastic gradient descent algorithm and test it using the next cell.**

In [ ]:
def sgd(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic gradient descent
    """
    mu = model.strength
    w = w0.copy()
    w_ave = w0.copy()
    callback(w)
    n_samples = model.n_samples
    for idx in range(n_iter):
        i = idx_samples[idx]
        
        #
        #
        # YOUR CODE HERE
        #
        #
        # every n_samples iterations
        if idx % n_samples == 0:
            callback(w)  #w_ave
    return w


send(sgd, 11)

In [ ]:
step = 0.1
callback_sgd = inspector(model, n_iter=n_iter)
w_sgd = sgd(model, w0, idx_samples, n_iter=model.n_samples * n_iter, 
            step=step, callback=callback_sgd)

**Which of the method is  the fastest during the  first 5 passes over the data?**

<a id='sag'></a>
## 3.6. Stochastic average gradient descent


**8) Finish the function `sag` below that implements the stochastic averaged gradient algorithm and test it using the next cell.**

In [ ]:
def sag(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic average gradient descent
    """
    w = w0.copy()
    n_samples, n_features = model.n_samples, model.n_features
    gradient_memory = np.zeros((n_samples, n_features)) # one gradient per sample n= 60k,  d= 50M  => 3 10^12
    y = np.zeros(n_features)
    callback(w)
    for idx in range(n_iter):
        i = idx_samples[idx]        
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        if idx % n_samples == 0:
            callback(w)
    return w
send(sag, 12)

In [ ]:
step = 1 / model.lip_max()
callback_sag = inspector(model, n_iter=n_iter)
w_sag = sag(model, w0, idx_samples, n_iter=model.n_samples * n_iter, 
            step=step, callback=callback_sag)

- What happens during the first pass of SAG?
- What is the main problem  of SAG?
- What is  the size of the gradient_memory matrix?

<a id='svrg'></a>
## 3.7. Stochastic variance reduced gradient

**9) Finish the function `svrg` below that implements the stochastic variance reduced gradient algorithm and test it using the next cell.**

In [ ]:
def svrg(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Stochastic variance reduced gradient descent
    """
    w = w0.copy()
    w_old = w.copy()
    temp_sum = 0
    n_samples = model.n_samples
    callback(w)
    for idx in range(n_iter):        
        
        #
        #
        # YOUR CODE HERE
        #
        #
        
        if idx % n_samples == 0:
            callback(w)
    return 
send(svrg, 13)

In [ ]:
step = 1 / model.lip_max()
callback_svrg = inspector(model, n_iter=n_iter)
w_svrg = svrg(model, w0, idx_samples, n_iter=model.n_samples * n_iter,
              step=step, callback=callback_svrg)

<a id='adagrad'></a>

## 3.8.1 ADAGRAD

**10) Create the function `adagrad` that implements the adagrad solver and test it.**

In [ ]:
##################


def adagrad(model, w0, n_iter, step, callback, verbose=True):
    """Adagrad"""

#
#
# YOUR CODE HERE
#
#

##################
send(adagrad, 14)

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

- What is the set of parameters for ADAGRAD? 
- What are default choices for those parameters?
- Is Adagrad typically implemented with deterministic or Stochastic Gradients?

In [ ]:
# Do/Shall we use  momentum for adagrad adadelta, etc?
# - we should
# - for simplicity, we don't

<a id='adagrad'></a>

## 3.8.2 ADAGRAD_Stochastic

**10 bis) Create the function `adagrad` that implements the adagrad solver and test it.**

In [ ]:
##################


def adagrad_Sto(model, w0, idx_samples, n_iter, step, callback, verbose=True):
    """Adagrad"""

#
#
# YOUR CODE HERE
#
#

##################
send(adagrad, 15)

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

<a id='rmsprop'></a>


## 3.9 RMSProp

**11) Create the function `rmsprop` that implements the RMSProp solver and test it.**

In [ ]:


def rmsprop(model, w0, n_iter, step, rho, epsilon, callback, verbose=True):
##################

#
#
# YOUR CODE HERE
#
#

##################
send(rmsprop, 16)

- What is the set of parameters for RMSPROP? 
- What are default choices for those parameters?
- Is RMSPROP typically implemented with deterministic or Stochastic Gradients?

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

<a id='adadelta'></a>

## 3.10 AdaDelta

**12) Create the function `adadelta` that implements adadelta solver and test it.**

In [ ]:
def adadelta(model, w0, n_iter, rho, epsilon, callback, verbose=True):
    ##################
    
    #
    #
    # YOUR CODE HERE
    #
    #
    
##################
send(adadelta, 17)

- What is the set of parameters for AdaDelta? 
- What are default choices for those parameters? Compare r= 0.95 and rho = 0.999

- What is Adadelta equivalent to for rho =1 (GD with step size 1)

- Is AdaDelta typically implemented with deterministic or Stochastic Gradients?

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

<a id='adam'></a>


## 3.11 Adam

**13) Create the function `adam` that implements the adam algorithm and test it.**

In [ ]:
def adam(model, w0, n_iter, step, beta1, beta2, epsilon, callback, verbose=True):
##################

#
#
# YOUR CODE HERE
#
#

##################
send(adam, 18)

- What is the set of parameters for Adam? 
- What are default choices for those parameters?
- Is Adam typically implemented with deterministic or Stochastic Gradients?

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

<a id='adamax'></a>


## 3.12 Adamax

**14) Create the function `adamax` that implements the adamax solver and test it.**

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################
send(adamax, 19)

In [ ]:
##################

#
#
# YOUR CODE HERE
#
#

##################

<a id='comparison'></a>
# 4. Comparison of all algorithms

**15) Plot the values of the loss for the different iteration and for each solver. Comment. **

In [ ]:
# Modify here to only call the methods you have implemented
callbacks = [callback_gd, callback_agd, callback_cgd, callback_sgd, 
             callback_sag, callback_svrg, 
             callback_adagrad, callback_rmsprop, callback_adadelta, callback_adam, callback_adamax]
names = ["GD", "AGD", "CGD", "SGD",
         "SAG", "SVRG", 
         "ADAGRAD", "RMSPROP", "ADADELTA",        "ADAM", "ADAMAX"]

### Let's look at the convergence curves

In [ ]:
plt.figure(figsize=(10, 10))

for callback, name in zip(callbacks, names):
    objectives = np.array(callback.objectives)
    objectives_dist = objectives 
    plt.plot(objectives_dist, label=name, lw=2)

plt.tight_layout()
plt.xlim((0, n_iter))
plt.xlabel("Number of passes on the data", fontsize=16)
plt.ylabel(r"$F(w^k) $", fontsize=16)
plt.legend(loc='lower left')
plt.tight_layout()
send(plt, 20)

### What do you think? How can we improve the plot to make it more insightful ?

In [ ]:
# 1 . Compute the minimal value of the function by running CGD (or another fast method)
# for 20 times more iterations than any other method

# 2. Set yscale to log

callback_long = inspector(model, n_iter=1000, verbose=False)
w_cgd = cgd(model, w0, n_iter=1000, callback=callback_long, verbose=False)
obj_min = callback_long.objectives[-1]

In [ ]:
plt.figure(figsize=(10, 10))
plt.yscale("log")

for callback, name in zip(callbacks, names):
    objectives = np.array(callback.objectives)
    objectives_dist = objectives - obj_min    
    plt.plot(objectives_dist, label=name, lw=2)

plt.tight_layout()
plt.xlim((0, n_iter))
plt.xlabel("Number of passes on the data", fontsize=16)
plt.ylabel(r"$F(w^k) - F(w^*)$", fontsize=16)
plt.legend(loc='lower left')
plt.tight_layout()
send(plt, 21)

Try to answer some of the following questions:

- A. What is the speed of convergence  of GD, AGD, SGD (you may need another plot for that)
- B. Compare GD SGD: is there any "best algorithm between GD and SGD"
- C. Compare GD and AGD. Compare the slopes? How does that reflect theory ? What steps did we choose?
- D. Which curve oscillates (i.e., is "bumpy")? check this great blog post on the topic https://distill.pub/2017/momentum/
- E. Tune the step size for GD, SGD, etc. FInd the value of the maximal step size that avoids divergence
- F. Compare the convergence rate for different strategies for SGD (learning rate decay, averaging or not)
- G. Compare the different strategies for the tuning of the momentum coefficient for AGD
- H. What is the impact of Variance reduction. Does it match what is expected?
- I. n logistic regression, study the influence of the correlation of the features on the performance of the optimization algorithms. Explain.
- J. In logistic regression, study the influence of the level of ridge penalization on the performance of the optimization algorithms. Explain.



### <font color='green'> If you generate interesting plots, share them  !! </font> 

Use 

````send(plt, 22)````

 (with increasing numbers starting at 30)